In [1]:
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer #用于从DNA序列中提取K-mer特征
from collections import Counter   #计算K-mer频率
from sklearn.ensemble import RandomForestClassifier    #随机森林
import xgboost as xgb                                  #XGboost
from sklearn.svm import SVC                            #SVM
from sklearn.metrics import accuracy_score,precision_score, f1_score
from sklearn.metrics import precision_score, recall_score

In [3]:
#DNA序列处理
sequences_list = []
current_sequence = ""

with open('./train_data.txt', 'r') as file:
    for line in file:
        if line.strip() and line[0].isdigit() and ':' in line:
            if current_sequence:
                sequences_list.append(current_sequence.replace("\n", ""))
            current_sequence = ""
        else:
            current_sequence += line.strip()
if current_sequence:
    sequences_list.append(current_sequence.replace("\n", ""))

In [7]:
#标签处理
labels_list = []
with open('./train_label.txt') as file:
    for line in file:
        labels_list.extend([int(label) for label in line.strip().split(',') if label.isdigit()])


In [ ]:
#碱基个数和频率统计
def sequence_statistics(sequences,labels):
    label_statistics = {}

    all_labels = set(labels)

    for label in all_labels:
        label_sequences = [sequence for sequence, seq_label in zip(sequences, labels) if seq_label == label]
        label_length = 0
        label_nucl_count = {}
        label_total_count = 0

        for sequence in label_sequences:
            length = len(sequence)
            label_length+=length

            for nucl in sequence:
                label_nucl_count[nucl] = label_nucl_count.get(nucl, 0) + 1
                label_total_count += 1

        label_nucl_frequency = {nucl: count / label_total_count for nucl, count in label_nucl_count.items()}

        label_statistics[label] = {
            "length": label_length,
            "nucl_count": label_nucl_count,
            "nucl_fre": label_nucl_frequency
        }

    return label_statistics

sequence_statistics(sequences_list,labels_list)

In [12]:
#K-mer
def generate_kmers(sequence, k):
    return [sequence[i:i+k] for i in range(len(sequence) - k + 1)]
k = 4
kmers_list = [generate_kmers(seq, k) for seq in sequences_list]

# 将K-mer列表转换为字符串，因为CountVectorizer需要字符串输入
kmers_as_string = [" ".join(kmer_list) for kmer_list in kmers_list]

In [16]:
#使用CountVectorizer提取特征并生成特征矩阵X，其中每一行代表一个DNA序列，每一列代表一个K-mer，值为该K-mer在该序列中出现的次数。
vectorizer = CountVectorizer()
X = vectorizer.fit_transform(kmers_as_string)
y = labels_list  # 标签列表
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
#词汇表
print(vectorizer.vocabulary_)

{'ataa': 48, 'taaa': 192, 'aaag': 2, 'aaga': 8, 'agag': 34, 'gagg': 138, 'aggg': 42, 'gggt': 171, 'ggta': 172, 'gtac': 177, 'tacg': 198, 'acga': 24, 'cgag': 98, 'gggg': 170, 'gggc': 169, 'ggcc': 165, 'gcca': 148, 'ccag': 82, 'cagc': 73, 'agct': 39, 'gctg': 158, 'ctgg': 122, 'tgga': 232, 'ggag': 162, 'gaga': 136, 'gagc': 137, 'agcc': 37, 'ccat': 83, 'catg': 78, 'atgc': 57, 'tgca': 228, 'gcag': 146, 'cagt': 75, 'agtc': 45, 'gtcc': 181, 'tcca': 212, 'ccaa': 80, 'caag': 66, 'aagc': 9, 'agcg': 38, 'gcgg': 154, 'cggg': 106, 'ggga': 168, 'ggat': 163, 'gatt': 143, 'attg': 62, 'ttgt': 251, 'tgtg': 238, 'gtga': 184, 'tgag': 226, 'ctgt': 123, 'gtgg': 186, 'tggt': 235, 'ggtg': 174, 'gtgt': 187, 'tgaa': 224, 'gaat': 131, 'aatc': 13, 'atcc': 53, 'caga': 72, 'agaa': 32, 'gaac': 129, 'aaca': 4, 'acaa': 16, 'aagg': 10, 'aggc': 41, 'ggcg': 166, 'cggc': 105, 'gcgc': 153, 'cgct': 103, 'gcgt': 155, 'cgtg': 110, 'tggg': 234, 'ggtc': 173, 'gtca': 180, 'tcag': 210, 'cagg': 74, 'agac': 33, 'gaca': 132, 'acag':

In [17]:
#输出特征矩阵X的稠密形式
X_dense = X.toarray()
print(X_dense)

[[ 2  2  4 ...  4  9  4]
 [ 3  1  1 ...  1  3  2]
 [ 4  3  3 ...  2  3  2]
 ...
 [18 17 15 ... 23 27 42]
 [ 3  3  6 ...  4  4  3]
 [ 6  8 11 ... 20 16 19]]


In [18]:
#对每个DNA序列计算K-mer频率（即每种K-mer在该序列中出现的频率）
def kmer_frequency(sequence, k):
    kmers = [sequence[i:i+k] for i in range(len(sequence) - k + 1)]
    total_kmers = len(kmers)
    kmer_count = Counter(kmers)
    return {kmer: count / total_kmers for kmer, count in kmer_count.items()}
k = 4
kmer_freq_list = [kmer_frequency(seq, k) for seq in sequences_list]

In [19]:
kmer_freq_list

[{'ATAA': 0.000628140703517588,
  'TAAA': 0.0018844221105527637,
  'AAAG': 0.002512562814070352,
  'AAGA': 0.000628140703517588,
  'AGAG': 0.005653266331658292,
  'GAGG': 0.008165829145728644,
  'AGGG': 0.009422110552763818,
  'GGGT': 0.008793969849246231,
  'GGTA': 0.0018844221105527637,
  'GTAC': 0.00314070351758794,
  'TACG': 0.002512562814070352,
  'ACGA': 0.002512562814070352,
  'CGAG': 0.00314070351758794,
  'GGGG': 0.007537688442211055,
  'GGGC': 0.01507537688442211,
  'GGCC': 0.013190954773869347,
  'GCCA': 0.011306532663316583,
  'CCAG': 0.010678391959798994,
  'CAGC': 0.015703517587939697,
  'AGCT': 0.007537688442211055,
  'GCTG': 0.020100502512562814,
  'CTGG': 0.013190954773869347,
  'TGGA': 0.00314070351758794,
  'GGAG': 0.0043969849246231155,
  'GAGA': 0.0037688442211055275,
  'GAGC': 0.005025125628140704,
  'AGCC': 0.007537688442211055,
  'CCAT': 0.005653266331658292,
  'CATG': 0.005653266331658292,
  'ATGC': 0.00314070351758794,
  'TGCA': 0.005025125628140704,
  'GCAG':

In [20]:
# 获取所有可能的k-mer组合
all_kmers = set()
for freq_dict in kmer_freq_list:
    all_kmers.update(freq_dict.keys())


In [26]:
len(all_kmers)

256

In [22]:
# 为每个序列生成一个包含所有k-mer频率的向量，作为其特征
feature_matrix = np.zeros((len(kmer_freq_list), len(all_kmers)))
for i, freq_dict in enumerate(kmer_freq_list):
    for j, kmer in enumerate(all_kmers):
        feature_matrix[i, j] = freq_dict.get(kmer, 0)

In [23]:
X = feature_matrix   #特征矩阵
y = labels_list      #标签

In [25]:
#X.shape

(3819, 256)

In [28]:
# 数据拆分
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [29]:
#随机森林模型
model = RandomForestClassifier()
model.fit(X_train, y_train)
#预测和评估
predictions = model.predict(X_test)
print("RandomForest Accuracy:", accuracy_score(y_test, predictions))


RandomForest Accuracy: 0.6387434554973822


In [30]:
#XGboost
y_train_adjusted = [label - 1 for label in y_train]
y_test_adjusted = [label - 1 for label in y_test]
xgb_model = xgb.XGBClassifier(use_label_encoder=False, eval_metric='mlogloss')
xgb_model.fit(X_train, y_train_adjusted)
# 进行预测
xgb_predictions = xgb_model.predict(X_test)
# 评估模型
xgb_predictions_adjusted = [pred + 1 for pred in xgb_predictions]
xgb_accuracy = accuracy_score(y_test, xgb_predictions_adjusted)
xgb_precision = precision_score(y_test, xgb_predictions_adjusted, average='weighted')
xgb_f1 = f1_score(y_test, xgb_predictions_adjusted, average='weighted')
print("XGBoost Accuracy:", xgb_accuracy)
print("XGBoost Precision:", xgb_precision)
print("XGBoost F1 Score:", xgb_f1)


XGBoost Accuracy: 0.7015706806282722
XGBoost Precision: 0.7039658824689013
XGBoost F1 Score: 0.6872973399628658


In [31]:
#SVM
# 创建并训练SVM模型
svm_model = SVC(kernel='poly',C=0.1)
svm_model.fit(X_train, y_train)
# 进行预测
svm_predictions = svm_model.predict(X_test)
# 评估模型
svm_accuracy = accuracy_score(y_test, svm_predictions)
svm_precision = precision_score(y_test, svm_predictions, average='weighted')
svm_f1 = f1_score(y_test, svm_predictions, average='weighted')
print("SVM Accuracy:", svm_accuracy)
print("SVM Precision:", svm_precision)
print("SVM F1 Score:", svm_f1)

SVM Accuracy: 0.7081151832460733
SVM Precision: 0.7070563674001968
SVM F1 Score: 0.6896987425681341


In [32]:
#读取测试数据
test_sequences_list = []
with open('./test_data.txt', 'r') as file:
    for line in file:
        if line.strip() and line[0].isdigit() and ':' in line:
            if current_sequence:
                test_sequences_list.append(current_sequence.replace("\n", ""))
            current_sequence = ""
        else:
            current_sequence += line.strip()
# 添加最后一个序列
if current_sequence:
    test_sequences_list.append(current_sequence.replace("\n", ""))

In [34]:
# 计算测试数据的K-mer频率
test_kmer_freq_list = [kmer_frequency(seq, k) for seq in test_sequences_list]
# 构建测试数据的特征矩阵
test_feature_matrix = np.zeros((len(test_kmer_freq_list), len(all_kmers)))
for i, freq_dict in enumerate(test_kmer_freq_list):
    for j, kmer in enumerate(all_kmers):
        test_feature_matrix[i, j] = freq_dict.get(kmer, 0)
X_test = test_feature_matrix

In [35]:
# 使用训练好的模型进行预测
test_predictions = svm_model.predict(X_test)
print(test_predictions)
set(test_predictions)


[1 1 2 2 1 1 1 1 1 1 2 1 2 1 1 1 3 1 1 1 1 3 1 1 2 1 1 1 2 1 1 3 1 1 1 1 2
 3 2 1 1 2 1 1 1 1 2 1 1 2 3 1 3 2 1 3 1 3 1 1 1 1 1 1 1 1 1 1 1 1 1 1 2 1
 1 1 1 1 1 3 1 1 1 3 1 1 1 1 1 1 2 1 2 1 3 2 1 1 3 3 1 1 3 1 1 2 2 1 1 1 2
 1 1 3 2 1 1 2 2 1 1 2 1 1 1 1 1 3 2 2 1 1 2 1 1 1 1 1 2 1 1 2 2 3 1 1 3 1
 1 1 1 1 1 3 3 1 3 3 1 1 1 1 1 1 1 2 1 1 1 1 1 1 1 1 1 2 2 3 2 2 1 3 1 1 1
 1 1 1 1 1 1 1 1 1 2 1 3 1 1 1 3 3 2 1 3 1 3 2 2 3 1 1 1 1 3 2 2 1 3 1 3 1
 1 2 3 1 1 1 1 1 2 1 1 3 1 2 2 1 1 1 2 1 2 2 1 1 1 1 1 3 1 1 1 1 1 2 1 1 2
 1 1 1 1 3 1 1 2 1 2 1 1 1 3 1 3 1 3 1 1 2 2 1 1 3 1 1 3 3 1 1 2 2 1 3 2 1
 1 1 1 1 3 1 1 1 1 1 3 2 1 2 1 1 1 2 1 1 3 2 3 1 1 2 1 1 1 1 1 3 3 1 1 2 1
 1 2 1 1 3 1 1 2 2 1 1 1 1 2 1 1 2 1 2 2 1 1 1 1 1 2 2 1 2 2 1 2 1 1 2 3 2
 1 1 3 2 3 1 3 1 1 1 1 1 1 2]


{1, 2, 3}

In [36]:
label_indices = {1: [], 2: [], 3: []}
for i, label in enumerate(test_predictions, 1):
    label_indices[label].append(i)


In [37]:
for label in label_indices:
    sequence_numbers = ','.join(map(str, label_indices[label]))
    print(f"标签{label}：({sequence_numbers})")


标签1：(1,2,5,6,7,8,9,10,12,14,15,16,18,19,20,21,23,24,26,27,28,30,31,33,34,35,36,40,41,43,44,45,46,48,49,52,55,57,59,60,61,62,63,64,65,66,67,68,69,70,71,72,74,75,76,77,78,79,81,82,83,85,86,87,88,89,90,92,94,97,98,101,102,104,105,108,109,110,112,113,116,117,120,121,123,124,125,126,127,131,132,134,135,136,137,138,140,141,145,146,148,149,150,151,152,153,156,159,160,161,162,163,164,165,167,168,169,170,171,172,173,174,175,181,183,184,185,186,187,188,189,190,191,192,193,194,196,198,199,200,204,206,211,212,213,214,218,220,222,223,226,227,228,229,230,232,233,235,238,239,240,242,245,246,247,248,249,251,252,253,254,255,257,258,260,261,262,263,265,266,268,270,271,272,274,276,278,279,282,283,285,286,289,290,293,296,297,298,299,300,302,303,304,305,306,309,311,312,313,315,316,320,321,323,324,325,326,327,330,331,333,334,336,337,339,340,343,344,345,346,348,349,351,354,355,356,357,358,361,364,366,367,371,372,376,378,379,380,381,382,383)
标签2：(3,4,11,13,25,29,37,39,42,47,50,54,73,91,93,96,106,107,111,115,1